### Imports:

In [1]:
from datetime import datetime, timedelta
import plotly.graph_objects as go
import MetaTrader5 as mt5
import pandas as pd
import numpy as np
import warnings
import json

### Inicializando:

In [2]:
warnings.filterwarnings("ignore", category=DeprecationWarning) 
warnings.filterwarnings("ignore", category=RuntimeWarning) 

In [3]:
def object_to_dict(obj):
    return {attr: getattr(obj, attr) for attr in dir(obj) if not attr.startswith("__") and not callable(getattr(obj, attr))}

def const_to_matrix(const, df, format="series"):
    return pd.Series([const for i in range(df.shape[0])]) if format == "series" else pd.DataFrame({"a": [2 for i in range(df.shape[0])]})

#def debbug_print(obj):
#    print(f'''Terminal info dict (len:{len(object_to_dict(obj))}):
#{json.dumps({attr: getattr(obj, attr) for attr in dir(obj) if not attr.startswith("__") and not callable(getattr(obj, attr))}, indent=2)}''')
    #for i in {attr: getattr(obj, attr) for attr in dir(obj)}: print(f'{i}')

In [4]:
# Verifica se a sessão foi iniciada e logada corretamente
if not mt5.initialize(login=3016470251, server="Rico-DEMO", password="Paranawe@123"):
    print("initialize() failed, error code =", mt5.last_error())
    quit()

# Dá display em todos os dados referentes ao terminal (5 a mais do que ele mandaria normalmente)
print(f'''Terminal info dict (len:{len(object_to_dict(mt5.terminal_info()))}):
{json.dumps({attr: getattr(mt5.terminal_info(), attr) for attr in dir(mt5.terminal_info()) if not attr.startswith("__") and not callable(getattr(mt5.terminal_info(), attr))}, indent=2)}''')

###############################################################################################################

# Ativo de análise
symbol = "TSLA34"

# Checa se há retorno do nome do ativo e pesquisa as posições abertas
positions=mt5.positions_get(symbol=symbol)
if positions == None:
    print(f"Posições não encontradas em {symbol}, error code={mt5.last_error()}")
else:
    # Imprime todas as posições abertas
    print(f"Total de posições com {symbol} = {len(positions)}")
    for position in positions:
        print(position)

###############################################################################################################

# Traz os dados do broker (atenção ao objeto "mt5.TIMEFRAME", e um range de 1041 dias é o renge máximo numa requisição única)
symbol = 'TSLA34'
timeFrame = mt5.TIMEFRAME_M15
dateFrom = datetime.now() - timedelta(1041)
dateTo = datetime.now()- timedelta(0)
df = pd.DataFrame(mt5.copy_rates_range(symbol, timeFrame, dateFrom, dateTo))
df["time"] = pd.to_datetime(df["time"], unit="s") # Converte de unix code para data e hora
display(df)
df.to_csv(f"Data Base\\{symbol}{datetime.today().strftime("%Y_%m_%d")}.csv", sep=',', quoting=1, index=False) 

###############################################################################################################

date_from = datetime(2023,1,1) 
date_to = datetime.now()

print(f"orders_total: {mt5.orders_total()}")                            # Total de ordens
print(f"positions_total: {mt5.positions_total()}")                         # Total de posições abertas
print(f"history_orders_total: {mt5.history_orders_total(date_from, date_to)}")  # Total de ordens no histórico de negociação
print(f"history_deals_total: {mt5.history_deals_total(date_from, date_to)}")   # Total de transações no histórico de negociação (deals)

# Finaliza a conexão com o  MetaTrader 5
mt5.shutdown()

Terminal info dict (len:25):
{
  "build": 5200,
  "codepage": 1252,
  "commondata_path": "C:\\Users\\Meu Computador\\AppData\\Roaming\\MetaQuotes\\Terminal\\Common",
  "community_account": false,
  "community_balance": 0.0,
  "community_connection": false,
  "company": "MetaQuotes Ltd.",
  "connected": true,
  "data_path": "C:\\Users\\Meu Computador\\AppData\\Roaming\\MetaQuotes\\Terminal\\D0E8209F77C8CF37AD8BF550E51FF075",
  "dlls_allowed": false,
  "email_enabled": false,
  "ftp_enabled": false,
  "language": "Portuguese (Brazil)",
  "maxbars": 100000,
  "mqid": false,
  "n_fields": 22,
  "n_sequence_fields": 22,
  "n_unnamed_fields": 0,
  "name": "MetaTrader 5",
  "notifications_enabled": false,
  "path": "C:\\Program Files\\MetaTrader 5",
  "ping_last": 5588,
  "retransmission": 0.0,
  "trade_allowed": false,
  "tradeapi_disabled": false
}
Total de posições com TSLA34 = 0


time   open   high    low  close  tick_volume  spread  \
0     2022-10-25 10:00:00  35.00  35.23  35.00  35.19          145       1   
1     2022-10-25 10:15:00  35.19  35.22  35.00  35.06          120       1   
2     2022-10-25 10:30:00  35.15  35.95  35.15  35.84          325       1   
3     2022-10-25 10:45:00  35.88  36.18  35.87  36.04          205       1   
4     2022-10-25 11:00:00  36.07  36.30  35.99  36.24          215       1   
...                   ...    ...    ...    ...    ...          ...     ...   
20868 2025-08-29 16:30:00  56.27  56.40  56.26  56.38          157       0   
20869 2025-08-29 16:45:00  56.39  56.53  56.39  56.50          157       0   
20870 2025-08-29 17:00:00  56.62  56.62  56.62  56.62            3       5   
20871 2025-08-29 18:15:00  56.61  56.61  56.20  56.22           27       1   
20872 2025-08-29 18:30:00  56.59  56.60  56.59  56.60            2      29   

       real_volume  
0            20042  
1            25108  
2           119083  
3            37066  
4           182374  
...            ...  
20868       126809  
20869        26374  
20870        45261  
20871        13655  
20872           15  

[20873 rows x 8 columns]

orders_total: 0
positions_total: 0
history_orders_total: 0
history_deals_total: 1


True

### Indicadores:

In [11]:
def create_moving_average(df, col_name:str, period:int, inplace:bool=False, decimals:int=2): 
    """Create a moving average column in a dataset, if already exists the column get updated.

    Args:
        df: The pandas.DataFrame object that will recieve the new column (e.g., df_stocks).
        col_name: The name of the column used as calculation base to get the average (e.g., "close").
        period: The candle range that the moving average will be calculated (e.g., 9).
        inplace: Not mandatory. If True create the column already in the pandas.DataFrame object (e.g., True).
        decimals: The number of the decimal values

    Returns:
        The column with the moving average calculated. Replaces pd.NA in all the first 'period' values."""

    processed_list = [round(sum([df[col_name][i-j] for j in range(period)]) / period, decimals) if i > period-2 else pd.NA for i in range(df.shape[0])]

    if inplace:
        df[f"moving_average_{col_name}({period})"] = processed_list
    else:
        return pd.DataFrame({f"moving_average_{col_name}({period})":processed_list})

########################################################################################################################################################

# Função para detectar se o candle é hammer (apesar do tamanho, é bem mais eficiente do que parece e roda em "C")
# Ela retorna "1", "0" e "-1" ao invés de True e False pois um candle pode ser hammer, mas a orientação de influencia nas propriedades do gráfico
# É considerado hammer todo candle que tem uma sombra de 2 a 3 vezes o tamanho do seu corpo

def create_hammer_detection(df, inplace:bool=False, open:str="open", close:str="close", low:str="low", high:str="high"):
    processed_list = [1 if 
    (df[high][i] - (df[close][i] + df[open][i] / 2)) / (df[high][i] - df[low][i]) < 0.3 and         # Checa se está de pé
    df[close][i] < df[open][i] and (df[close][i] - df[low][i]) / (df[open][i] - df[close][i]) > 3   # Checa se é martelo verde
    else 1 if 
    (df[high][i] - (df[close][i] + df[open][i] / 2)) / (df[high][i] - df[low][i]) < 0.3 and         # Checa se está de ponta-cabeça
    df[close][i] > df[open][i] and (df[open][i] - df[low][i]) / (df[close][i] - df[open][i]) > 3    # Checa se é martelo vermelho
    else -1 if 
    ((df[close][i] + df[open][i] / 2) - df[low][i]) / (df[high][i] - df[low][i]) < 0.3 and          # Checa se está de ponta-cabeça
    df[close][i] < df[open][i] and (df[high][i] - df[open][i]) / (df[open][i] - df[close][i]) > 3   # Checa se é martelo verde
    else -1 if 
    ((df[close][i] + df[open][i] / 2) - df[low][i]) / (df[high][i] - df[low][i]) < 0.3 and          # Checa se está de pé
    df[close][i] > df[open][i] and (df[high][i] - df[close][i]) / (df[close][i] - df[open][i]) > 3  # Checa se é martelo vermelho
    else 0 for i in range(df.shape[0])]

    if inplace:
        df["detecton_hammer"] = processed_list
    else:
        return pd.DataFrame({"detecton_hammer":processed_list})
    
########################################################################################################################################################


### Strategies:

##### MA Tradeview

In [8]:
def create_exponential_moving_average()

SyntaxError: expected ':' (104786041.py, line 1)

##### Create Cross Moving Average Strategy:

In [12]:
create_moving_average(df, "close", 9, inplace=True)
create_moving_average(df, "close", 21, inplace=True)

df["strtgy_ma"] = [pd.NA] + [
    pd.NA if any(pd._libs.missing.NAType == type(i) for i in [df["moving_average_close(9)"][i], df["moving_average_close(21)"][i], df["moving_average_close(9)"][i-1], df["moving_average_close(21)"][i-1]])
    else 1 if df["moving_average_close(9)"][i] > df["moving_average_close(21)"][i] and df["moving_average_close(9)"][i-1] < df["moving_average_close(21)"][i-1]
    else -1 if df["moving_average_close(9)"][i] < df["moving_average_close(21)"][i] and df["moving_average_close(9)"][i-1] > df["moving_average_close(21)"][i-1]
    else 1 if df["moving_average_close(9)"][i] == df["moving_average_close(21)"][i] and df["moving_average_close(9)"][i-1] < df["moving_average_close(21)"][i-1]
    else -1 if df["moving_average_close(9)"][i] == df["moving_average_close(21)"][i] and df["moving_average_close(9)"][i-1] > df["moving_average_close(21)"][i-1]
    else 0 for i in range(1, df.shape[0])]

In [13]:
ma_strategy_df = df[df["strtgy_ma"] != 0].dropna()
ma_strategy_df.reset_index(drop=True, inplace=True)
ma_strategy_df

time   open   high    low  close  tick_volume  spread  \
0    2022-10-25 15:45:00  36.81  36.90  36.74  36.82          370       1   
1    2022-10-25 16:15:00  36.93  37.06  36.90  37.00          484       1   
2    2022-10-26 15:30:00  37.82  37.96  37.78  37.78          100       1   
3    2022-10-27 10:30:00  38.32  38.99  37.72  38.29          494       1   
4    2022-10-27 10:45:00  38.29  38.44  37.21  37.34          221       1   
...                  ...    ...    ...    ...    ...          ...     ...   
1138 2025-08-22 10:00:00  54.87  54.87  54.80  54.83          112       1   
1139 2025-08-26 11:15:00  58.59  58.80  58.50  58.55          238       1   
1140 2025-08-26 12:30:00  58.93  58.93  58.37  58.64          118       1   
1141 2025-08-26 12:45:00  58.65  58.68  58.60  58.60           18       1   
1142 2025-08-27 14:15:00  59.41  59.43  59.35  59.42           45       1   

      real_volume moving_average_close(9) moving_average_close(21) strtgy_ma  
0           31415                   36.63                    36.63        -1  
1          102871                   36.71                    36.71         1  
2           19131                   37.83                    37.92        -1  
3          125824                   37.95                    37.94         1  
4           57210                    37.9                     37.9        -1  
...           ...                     ...                      ...       ...  
1138        25415                   54.95                    54.95         1  
1139        64198                   58.62                    58.64        -1  
1140        68758                    58.7                    58.69         1  
1141         6937                   58.68                    58.68        -1  
1142        66756                   59.64                    59.69        -1  

[1143 rows x 11 columns]

##### Persist Strategies Data Consistency:

In [14]:
def process_strategy_consistency(df, strategy:str, display_result:bool=False):
    runs = 0
    while True:
        try:
            for i in range(1, df.shape[0]):
                df.reset_index(drop=True, inplace=True)
                if df[strategy][i] == df[strategy][i-1]:
                    if display_result: print(f"Linha deletada:\n{df.loc[[i]]};\n\nLinha anterior:\n{df.loc[[i-1]]}\n")
                    df.drop(i, inplace=True)
            runs += 1; break
        except KeyError: runs += 1

    if display_result: 
        display(f"O programa processou {runs} vezes")

In [15]:
process_strategy_consistency(ma_strategy_df, strategy="strtgy_ma", display_result=True)
ma_strategy_df

Linha deletada:
                  time   open   high    low  close  tick_volume  spread  \
54 2022-12-02 13:15:00  31.36  31.53  31.33  31.52           31       1   

    real_volume moving_average_close(9) moving_average_close(21) strtgy_ma  
54         3759                   31.51                    31.46         1  ;

Linha anterior:
                  time   open   high    low  close  tick_volume  spread  \
53 2022-12-02 10:00:00  31.68  31.92  31.67  31.84          158       1   

    real_volume moving_average_close(9) moving_average_close(21) strtgy_ma  
53        68468                   31.56                    31.56         1  

Linha deletada:
                  time  open   high    low  close  tick_volume  spread  \
74 2022-12-19 10:00:00  25.7  25.76  25.52  25.52          336       1   

    real_volume moving_average_close(9) moving_average_close(21) strtgy_ma  
74       179380                   24.99                    24.96         1  ;

Linha anterior:
                  

'O programa processou 3 vezes'

time   open   high    low  close  tick_volume  spread  \
0    2022-10-25 15:45:00  36.81  36.90  36.74  36.82          370       1   
1    2022-10-25 16:15:00  36.93  37.06  36.90  37.00          484       1   
2    2022-10-26 15:30:00  37.82  37.96  37.78  37.78          100       1   
3    2022-10-27 10:30:00  38.32  38.99  37.72  38.29          494       1   
4    2022-10-27 10:45:00  38.29  38.44  37.21  37.34          221       1   
...                  ...    ...    ...    ...    ...          ...     ...   
1090 2025-08-21 13:30:00  54.88  54.93  54.82  54.91           26       1   
1091 2025-08-22 10:00:00  54.87  54.87  54.80  54.83          112       1   
1092 2025-08-26 11:15:00  58.59  58.80  58.50  58.55          238       1   
1093 2025-08-26 12:30:00  58.93  58.93  58.37  58.64          118       1   
1094 2025-08-26 12:45:00  58.65  58.68  58.60  58.60           18       1   

      real_volume moving_average_close(9) moving_average_close(21) strtgy_ma  
0           31415                   36.63                    36.63        -1  
1          102871                   36.71                    36.71         1  
2           19131                   37.83                    37.92        -1  
3          125824                   37.95                    37.94         1  
4           57210                    37.9                     37.9        -1  
...           ...                     ...                      ...       ...  
1090         4903                   55.14                    55.14        -1  
1091        25415                   54.95                    54.95         1  
1092        64198                   58.62                    58.64        -1  
1093        68758                    58.7                    58.69         1  
1094         6937                   58.68                    58.68        -1  

[1095 rows x 11 columns]

In [18]:
def create_ma_gains(df, year:int, inplace=False):
    df = df[df["time"] > datetime(year, 1, 1)][df[df["time"] > datetime(year, 1, 1)]["time"] < datetime(year+1, 1, 1)].reset_index(drop=True)
    df["ma_gains"] = [(float(df["close"][i]) - float(df["close"][i-1])) / float(df["close"][i-1]) if df["strtgy_ma"][i] == -1 else np.NAN for i in range(df.shape[0])]
    df

In [32]:
ma_strategy_df["ma_gains"] = [(float(ma_strategy_df["close"][i]) - float(ma_strategy_df["close"][i-1])) / float(ma_strategy_df["close"][i-1]) if ma_strategy_df["strtgy_ma"][i] == -1 else np.NAN for i in range(ma_strategy_df.shape[0])]
ma_strategy_df

KeyError: -1

In [31]:
ma_strategy_df["actual_value(ma_gains)"]

KeyError: 'actual_value(ma_gains)'

In [30]:
for i in [2022, 2023, 2024, 2025]:    
    #create_ma_gains(ma_strategy_df, i)
    result_df = ma_strategy_df[ma_strategy_df["time"] > datetime(i, 1, 1)][ma_strategy_df[ma_strategy_df["time"] > datetime(i, 1, 1)]["time"] < datetime(i+1, 1, 1)].reset_index(drop=True)
    print(f'{i}:')
    print(f'Soma total: {sum([i for i in result_df["ma_gains"].dropna()]) * 100} %')
    print(f'Soma dos ganhos: {sum([j for j in [i if i > 0 else 0 for i in result_df["ma_gains"].dropna()] if j != 0]) * 100} %')
    print(f'Soma das perdas: {sum([j for j in [i if i < 0 else 0 for i in result_df["ma_gains"].dropna()] if j != 0]) * 100} %')
    print("")
    print(f'Quantidade de operações: {len([i for i in result_df["ma_gains"].dropna()])}')
    print(f'Quantidade de ganhos: {len([j for j in [i if i > 0 else 0 for i in result_df["ma_gains"].dropna()] if j != 0])}; ({len([j for j in [i if i > 0 else 0 for i in result_df["ma_gains"].dropna()] if j != 0]) / len([i for i in result_df["ma_gains"].dropna()]) * 100}%)')
    print(f'Quantidade de perdas: {len([j for j in [i if i < 0 else 0 for i in result_df["ma_gains"].dropna()] if j != 0])}; ({len([j for j in [i if i < 0 else 0 for i in result_df["ma_gains"].dropna()] if j != 0]) / len([i for i in result_df["ma_gains"].dropna()]) * 100}%)')
    print("")

2022:


KeyError: 'ma_gains'

In [29]:
def calculate_strategy(df, buy_signal="1", sell_signal="-1", strategy_column=""):
    if strategy_column:
        df[f"calc({strategy_column})"] = [0] + ["__" if df["close"][i] == buy_signal else "__" if df["close"][i] == buy_signal else "__" for i in range(1, df.shape[0])]

    else:
        for k in [j for j in [i if i.startswith("strtgy") else None for i in df.columns] if j is not None]:

SyntaxError: incomplete input (3367357032.py, line 6)

##### Runge Kutta:

In [28]:
col="close"
rk_step=2
derivation_step=1

test = pd.DataFrame({"a": [pd.NA for i in range(derivation_step + int(rk_step/2))] + [(float(float(df[col][i-int(rk_step/2)]) + float(df["k1"][i])/2) - float(df[col][i-int(rk_step/2)-derivation_step]))*rk_step for i in range(derivation_step + int(rk_step/2)+1, int(df.shape[0]))]})
test[[True if type(i) == type(pd.NA) else False for i in test["a"]]]

KeyError: 'k1'

In [27]:
a = [pd.NA for i in range(derivation_step + int(rk_step/2))] + [(float(float(df[col][i-int(rk_step/2)]) + float(df["k1"][i])/2) - float(df[col][i-int(rk_step/2)-derivation_step]))*rk_step for i in range(derivation_step + int(rk_step/2)+1, int(df.shape[0]))]
print(a[:4])
print(a[-4:])

KeyError: 'k1'

In [33]:
#df["derivative"] = [pd.NA for i in range(derivation_step)] + [float(df[col][i]) - float(df[col][i-derivation_step])*rk_step for i in range(derivation_step, df.shape[0])]
def create_runge_kutta(df, col:str="close", rk_step:int=2, derivation_step:int=1, inplace=True, error=False):
    if rk_step % 2 == 1:
        raise Exception("Odd rk_step not permited.")
    
    df["k1"] = [pd.NA for i in range(derivation_step + rk_step)] + [(float(df[col][i-rk_step]) - float(df[col][i-rk_step-derivation_step]))*rk_step for i in range(derivation_step + rk_step, df.shape[0])]
    df["k2"] = [pd.NA for i in range(derivation_step + int(rk_step/2))] + [(float(float(df[col][i-int(rk_step/2)]) + float(df["k1"][i])/2) - float(df[col][i-int(rk_step/2)-derivation_step]))*rk_step for i in range(derivation_step + int(rk_step/2)+1, int(df.shape[0]))]
    df["k3"] = [pd.NA for i in range(derivation_step + int(rk_step/2))] + [(float(float(df[col][i-int(rk_step/2)]) + float(df["k2"][i])/2) - float(df[col][i-int(rk_step/2)-derivation_step]))*rk_step for i in range(derivation_step + int(rk_step/2)+1, int(df.shape[0]))]
    df["k4"] = [
        pd.NA for i in range(derivation_step)
        ] + [
            (
                float(
                    float(
                        df[col][i]
                    ) + float(
                        df["k3"][i]
                    )
                ) - float(
                    df[col][i-derivation_step]
                )
            )*rk_step for i in range(
                derivation_step, int(df.shape[0]) - rk_step
            )
            ]
        
    rk_list = [pd.NA for i in range(derivation_step)] + [float(float(df["k1"][i] + 2*df["k2"][i] + 2*df["k3"][i] + df["k4"][i])/6) + float(df[col][i]) for i in range(derivation_step, int(df.shape[0]) - rk_step)] + [pd.NA for i in range(rk_step)]
    error_list = [pd.NA for i in range(derivation_step)] + [float(rk_list[i]) - float(df[col][i+1]) for i in range(derivation_step, int(df.shape[0]) - rk_step)] + [pd.NA for i in range(rk_step)]
    euler_list = [pd.NA for i in range(derivation_step)] + [float(df["k1"][i]) + float(df[col][i]) for i in range(derivation_step, int(df.shape[0]))]

    if inplace:
        df[f"rk_{col}({rk_step}, {derivation_step})"] = rk_list
        df[f"euler_{col}({derivation_step})"] = euler_list
        if error:
            df[f"rk_error_{col}({rk_step}, {derivation_step})"] = error_list
        df.drop(["k1", "k2", "k3", "k4"], axis=1, inplace=True)
    else:
        if error:
            return pd.DataFrame({f"rk_{col}({rk_step}, {derivation_step})":rk_list}), pd.DataFrame({f"rk_error_{col}({rk_step}, {derivation_step})":error_list})
        else:
            return pd.DataFrame({f"rk_{col}({rk_step}, {derivation_step})":rk_list}), pd.DataFrame({f"euler_{col}({derivation_step})":euler_list})

In [34]:
#df["derivative"] = [pd.NA for i in range(derivation_step)] + [float(df[col][i]) - float(df[col][i-derivation_step])*rk_step for i in range(derivation_step, df.shape[0])]
def create_runge_kutta(df, col:str="close", rk_step:int=2, derivation_step:int=1, inplace=True, error=False):
    if rk_step % 2 == 1:
        raise Exception("Odd rk_step not permited.")
    
    df["k1"] = [pd.NA for i in range(derivation_step + rk_step)] + [(df[col][i-rk_step+derivation_step]- df[col][i-rk_step-derivation_step])/2 for i in range(derivation_step + rk_step, df.shape[0])]
    df["k2"] = [pd.NA for i in range(derivation_step + rk_step)] + [((df[col][i+derivation_step-int(rk_step/2)] - df[col][i-derivation_step-int(rk_step/2)])/2) + df["k1"][i] for i in range(derivation_step + rk_step, df.shape[0])]
    df["k3"] = [pd.NA for i in range(derivation_step + rk_step)] + [((df[col][i+derivation_step-int(rk_step/2)] - df[col][i-derivation_step-int(rk_step/2)])/2) + df["k2"][i] for i in range(derivation_step + rk_step, df.shape[0])]
    df["k4"] = [
        pd.NA for i in range(derivation_step + rk_step)
    ] + [
        (
            float(
                float(
                    df[col][i]
                ) + float(
                    df["k3"][i]
                )
            ) - float(
                df[col][i-derivation_step]
            )
        )*rk_step for i in range(
            derivation_step + rk_step, int(df.shape[0])# - rk_step
        )
    ]
     
    rk_list = [pd.NA for i in range(derivation_step + rk_step)] + [float(float(df["k1"][i] + 2*df["k2"][i] + 2*df["k3"][i] + df["k4"][i])/6) + float(df[col][i]) for i in range(derivation_step + rk_step, int(df.shape[0]) - rk_step)]
    error_list = [pd.NA for i in range(derivation_step + rk_step)] + [float(rk_list[i]) - float(df[col][i+1]) for i in range(derivation_step + rk_step, int(df.shape[0]) - rk_step)]
    euler_list = [pd.NA for i in range(derivation_step + rk_step)] + [float(df["k1"][i]) + float(df[col][i]) for i in range(derivation_step + rk_step, int(df.shape[0]))]

    if inplace:
        df[f"rk_{col}({rk_step}, {derivation_step})"] = rk_list
        df[f"euler_{col}({derivation_step})"] = euler_list
        if error:
            df[f"rk_error_{col}({rk_step}, {derivation_step})"] = error_list
        df.drop(["k1", "k2", "k3", "k4"], axis=1, inplace=True)
    else:
        if error:
            return pd.DataFrame({f"rk_{col}({rk_step}, {derivation_step})":rk_list}), pd.DataFrame({f"rk_error_{col}({rk_step}, {derivation_step})":error_list})
        else:
            return pd.DataFrame({f"rk_{col}({rk_step}, {derivation_step})":rk_list}), pd.DataFrame({f"euler_{col}({derivation_step})":euler_list})

In [35]:
#df["derivative"] = [pd.NA for i in range(derivation_step)] + [float(df[col][i]) - float(df[col][i-derivation_step])*rk_step for i in range(derivation_step, df.shape[0])]
def create_runge_kutta(df, col:str="close", rk_step:int=2, derivation_step:int=1, inplace=True, error=False):
    if rk_step % 2 == 1:
        raise Exception("Odd rk_step not permited.")
    
    df["k1"] = [pd.NA for i in range(derivation_step)] + [(float(df[col][i]) - float(df[col][i-derivation_step]))*rk_step for i in range(derivation_step, df.shape[0])]
    df["k2"] = [pd.NA for i in range(derivation_step)] + [(float(float(df[col][i+int(rk_step/2)]) + float(df["k1"][i])/2) - float(df[col][i+int(rk_step/2)-derivation_step]))*rk_step for i in range(derivation_step, int(df.shape[0]) - int(rk_step/2))] + [pd.NA for i in range(int(rk_step/2))]
    df["k3"] = [pd.NA for i in range(derivation_step)] + [(float(float(df[col][i+int(rk_step/2)]) + float(df["k2"][i])/2) - float(df[col][i+int(rk_step/2)-derivation_step]))*rk_step for i in range(derivation_step, int(df.shape[0]) - int(rk_step/2))] + [pd.NA for i in range(int(rk_step/2))]
    df["k4"] = [pd.NA for i in range(derivation_step)] + [(float(float(df[col][i+rk_step]) + float(df["k3"][i])) - float(df[col][i+rk_step-derivation_step]))*rk_step for i in range(derivation_step, int(df.shape[0]) - rk_step)] + [pd.NA for i in range(rk_step)]
        
    rk_list = [pd.NA for i in range(derivation_step)] + [float(float(df["k1"][i] + 2*df["k2"][i] + 2*df["k3"][i] + df["k4"][i])/6) + float(df[col][i]) for i in range(derivation_step, int(df.shape[0]) - rk_step)] + [pd.NA for i in range(rk_step)]
    error_list = [pd.NA for i in range(derivation_step)] + [float(rk_list[i]) - float(df[col][i+1]) for i in range(derivation_step, int(df.shape[0]) - rk_step)] + [pd.NA for i in range(rk_step)]
    euler_list = [pd.NA for i in range(derivation_step)] + [float(df["k1"][i]) + float(df[col][i]) for i in range(derivation_step, int(df.shape[0]))]

    if inplace:
        df[f"rk_{col}({rk_step}, {derivation_step})"] = rk_list
        df[f"euler_{col}({derivation_step})"] = euler_list
        if error:
            df[f"rk_error_{col}({rk_step}, {derivation_step})"] = error_list
        df.drop(["k1", "k2", "k3", "k4"], axis=1, inplace=True)
    else:
        if error:
            return pd.DataFrame({f"rk_{col}({rk_step}, {derivation_step})":rk_list}), pd.DataFrame({f"rk_error_{col}({rk_step}, {derivation_step})":error_list})
        else:
            return pd.DataFrame({f"rk_{col}({rk_step}, {derivation_step})":rk_list}), pd.DataFrame({f"euler_{col}({derivation_step})":euler_list})

In [36]:
df["k1"].min()
df[df["k1"] == df["k1"].min()]

KeyError: 'k1'

In [37]:
create_runge_kutta(df, rk_step=2, derivation_step=1, inplace=False, error=True)

(      rk_close(2, 1)
 0               <NA>
 1          32.536667
 2              33.19
 3          32.893333
 4               31.8
 ...              ...
 20829      59.206667
 20830      59.133333
 20831      59.266667
 20832           <NA>
 20833           <NA>
 
 [20834 rows x 1 columns],
       rk_error_close(2, 1)
 0                     <NA>
 1                -1.103333
 2                     -0.5
 3                -0.556667
 4                    -1.31
 ...                    ...
 20829            -0.243333
 20830            -0.286667
 20831            -0.133333
 20832                 <NA>
 20833                 <NA>
 
 [20834 rows x 1 columns])

In [ ]:
std = 1.5

fig = go.Figure()
fig.update_layout(
    title="Teste de Runge Kuttas",
    xaxis_title="Erro em porcentagem",
    yaxis_title="Contagem",
    font_color="#cccccc", 
    plot_bgcolor='#1f1f1f', 
    paper_bgcolor='#181818',
    barmode='overlay'
)

for i in range(1, 3):
    for j in range(1, 3):
        rk_result, error = create_runge_kutta(df, rk_step=i*2, derivation_step=j, inplace=False, error=True)
        #print(sum([float(i) for i in create_runge_kutta(df, rk_step=i*2, derivation_step=j, inplace=False, error=True)[0][f"rk_close({i*2}, {j})"].dropna()])/int(len([float(i) for i in create_runge_kutta(df, rk_step=i*2, derivation_step=j, inplace=False, error=True)[0][f"rk_close({i*2}, {j})"].dropna()])))
        data = pd.Series([float(i)/0.38682969 for i in rk_result[[i for i in rk_result][0]].dropna(inplace=False)])

        fig.add_trace(
            go.Histogram(
                opacity=0.2, 
                name=f"RK Error (rk_step={i*2}, derivation_step={j})", 
                x=pd.Series([float(i) for i in error[[i for i in error][0]].dropna(inplace=False)]), 
                xbins=dict(start=np.ceil(-(data.describe()["std"])*std), end=np.ceil((data.describe()["std"])*std) + 0.1, size=0.1)
            )
        )

fig.show()

40.8464924071496
40.854229636741884
40.8783025269256
40.91980827091736


### RK NEW

In [13]:
#df["derivative"] = [pd.NA] + [float(df[col][i]) - float(df[col][i-1])*rk_step for i in range(1, df.shape[0])]
def create_runge_kutta(df, col:str="close", rk_step=2, inplace:bool=True, error:bool=False, direction:bool=False):
    if rk_step % 2 == 1:
        raise Exception("Odd rk_step not permited.")
    
    df["k1"] = [pd.NA for i in range(2)] + [((df[col][i])-(df[col][i-2]))/2 for i in range(2, df.shape[0])]
    df["k2"] = [pd.NA for i in range(2)] + [(df[col][i])-((df[col][i-1])+(df["k1"][i]/2)) for i in range(2, df.shape[0])]
    df["k3"] = [pd.NA for i in range(2)] + [(df[col][i])-((df[col][i-1])+(df["k2"][i])) for i in range(2, df.shape[0])]
    df["k4"] = [pd.NA for i in range(2)] + [(df[col][i])-((df[col][i-1])+(df["k1"][i])) for i in range(2, df.shape[0])]
     
    rk_list = [pd.NA for i in range(2)] + [float(float(df["k1"][i] + 2*df["k2"][i] + 2*df["k3"][i] + df["k4"][i])/6) + float(df[col][i]) for i in range(2, int(df.shape[0]))]
    error_list = [pd.NA for i in range(2)] + [float(rk_list[i]) - float(df[col][i+1]) for i in range(1 + 1, int(df.shape[0]) - 1)] + [pd.NA]
    direction_list = [pd.NA for i in range(3)] + [1 if (float(rk_list[i]) > float(df[col][i])) == (float(df[col][i+1]) > float(df[col][i])) else f"0 - P:{rk_list[i]}; R:{df[col][i]}; T:{df[col][i+1]}" for i in range(1 + rk_step, int(df.shape[0]) - 1)] + [pd.NA]
    
    #euler_list = [pd.NA for i in range(2)] + [float(df["k1"][i]) + float(df[col][i]) for i in range(1 + rk_step, int(df.shape[0]))]

    if inplace:
        df[f"rk_{col}({rk_step})"] = rk_list
        df.drop(["k1", "k2", "k3", "k4"], axis=1, inplace=True)
        #df[f"euler_{col}({1})"] = euler_list
        if error:
            df[f"rk_error_{col}({rk_step})"] = error_list
        if direction:
            df[f"rk_direction_{col}({rk_step})"] = direction_list
    else:
        if error and direction:
            return pd.DataFrame({f"rk_{col}({rk_step})":rk_list}), pd.DataFrame({f"rk_error_{col}({rk_step})":error_list}), pd.DataFrame({f"rk_direction_{col}({rk_step})":direction_list})
        elif error:
            return pd.DataFrame({f"rk_{col}({rk_step})":rk_list}), pd.DataFrame({f"rk_error_{col}({rk_step})":error_list})
        elif direction:
            return pd.DataFrame({f"rk_{col}({rk_step})":rk_list}), pd.DataFrame({f"rk_direction_{col}({rk_step})":direction_list})
        else:
            return pd.DataFrame({f"rk_{col}({rk_step})":rk_list})

In [ ]:
#df["derivative"] = [pd.NA] + [float(df[col][i]) - float(df[col][i-1])*rk_step for i in range(1, df.shape[0])]
def create_runge_kutta(df, col:str="close", rk_step=2, inplace:bool=True, error:bool=False, direction:bool=False):
    if rk_step % 2 == 1:
        raise Exception("Odd rk_step not permited.")
    
    df["k1"] = [pd.NA for i in range(2)] + [(((df[col][i-2+rk_step])-(8*(df[col][i-1+rk_step])))+((8*(df[col][i+1+rk_step]))-(df[col][i+2+rk_step])))/12 for i in range(2, df.shape[0])]
    df["k2"] = [pd.NA for i in range(2)] + [(df[col][i])-((df[col][i-1])+(df["k1"][i]/2)) for i in range(2, df.shape[0])]
    df["k3"] = [pd.NA for i in range(2)] + [(df[col][i])-((df[col][i-1])+(df["k2"][i])) for i in range(2, df.shape[0])]
    df["k4"] = [pd.NA for i in range(2)] + [(df[col][i])-((df[col][i-1])+(df["k1"][i])) for i in range(2, df.shape[0])]
     
    rk_list = [pd.NA for i in range(2)] + [float(float(df["k1"][i] + 2*df["k2"][i] + 2*df["k3"][i] + df["k4"][i])/6) + float(df[col][i]) for i in range(2, int(df.shape[0]))]
    error_list = [pd.NA for i in range(2)] + [float(rk_list[i]) - float(df[col][i+1]) for i in range(1 + 1, int(df.shape[0]) - 1)] + [pd.NA]
    direction_list = [pd.NA for i in range(3)] + [1 if (float(rk_list[i]) > float(df[col][i])) == (float(df[col][i+1]) > float(df[col][i])) else f"0 - P:{rk_list[i]}; R:{df[col][i]}; T:{df[col][i+1]}" for i in range(1 + rk_step, int(df.shape[0]) - 1)] + [pd.NA]
    
    #euler_list = [pd.NA for i in range(2)] + [float(df["k1"][i]) + float(df[col][i]) for i in range(1 + rk_step, int(df.shape[0]))]

    if inplace:
        df[f"rk_{col}({rk_step})"] = rk_list
        df.drop(["k1", "k2", "k3", "k4"], axis=1, inplace=True)
        #df[f"euler_{col}({1})"] = euler_list
        if error:
            df[f"rk_error_{col}({rk_step})"] = error_list
        if direction:
            df[f"rk_direction_{col}({rk_step})"] = direction_list
    else:
        if error and direction:
            return pd.DataFrame({f"rk_{col}({rk_step})":rk_list}), pd.DataFrame({f"rk_error_{col}({rk_step})":error_list}), pd.DataFrame({f"rk_direction_{col}({rk_step})":direction_list})
        elif error:
            return pd.DataFrame({f"rk_{col}({rk_step})":rk_list}), pd.DataFrame({f"rk_error_{col}({rk_step})":error_list})
        elif direction:
            return pd.DataFrame({f"rk_{col}({rk_step})":rk_list}), pd.DataFrame({f"rk_direction_{col}({rk_step})":direction_list})
        else:
            return pd.DataFrame({f"rk_{col}({rk_step})":rk_list})

In [34]:
i = 8
display(df.close[i-4:i+5])
display(f"Calculando a derivada de {df.close[i]} para {df.close[i+1]}")

derivadaA = (df.close[i+1] - df.close[i-1])/2
display(f"Derivada Centrada (passo 1): {derivadaA}; Previsto: {df.close[i] + derivadaA}; Erro: {(df.close[i] + derivadaA - df.close[i+1]) / df.close[i+1] * 100}")

derivadaB = (df.close[i+2] - df.close[i-2])/4
display(f"Derivada Centrada (passo 2): {derivadaB}; Previsto: {df.close[i] + derivadaB}; Erro: {(df.close[i] + derivadaB - df.close[i+1]) / df.close[i+1] * 100}")

derivadaC = (df.close[i-2] - 8*df.close[i-1] + 8*df.close[i+1] - df.close[i+2])/12
display(f"Derivada Centrada de 4: {derivadaC}; Previsto: {df.close[i] + derivadaC}; Erro: {(df.close[i] + derivadaC - df.close[i+1]) / df.close[i+1] * 100}")

derivadaD = (df.close[i-4] - 8*df.close[i-2] + 8*df.close[i+2] - df.close[i+4])/24
display(f"Derivada Centrada de 4 (passo 2): {derivadaD}; Previsto: {df.close[i] + derivadaD}; Erro: {(df.close[i] + derivadaD - df.close[i+1]) / df.close[i+1] * 100}")

#derivadaE = (df.close[i-2] - 8*df.close[i-1] + 8*df.close[i+1] - df.close[i+2])/144
#display(f"Derivada Centrada de 8): {derivadaE}; Previsto: {df.close[i] + derivadaE}; Erro: {(df.close[i] + derivadaE - df.close[i+1]) / df.close[i+1] * 100}")

passo = 2
derivadaF = (-(df.close[i+4*passo])+8*(df.close[i+3*passo])-28*(df.close[i+2*passo])+56*(df.close[i+passo])-70*(df.close[i])+56*(df.close[i-passo])-28*(df.close[i-2*passo])+8*(df.close[i-3*passo])-(df.close[i-4*passo]))/280/passo
display(f"Derivada Centrada de 8): {derivadaF}; Previsto: {df.close[i] + derivadaF}; Erro: {(df.close[i] + derivadaF - df.close[i+1]) / df.close[i+1] * 100}")

derivadaMedia = (derivadaA + derivadaB + derivadaC + derivadaD + derivadaF)/5
display(f"Derivada Média Geral: {derivadaMedia}; Previsto: {df.close[i] + derivadaMedia}; Erro: {(df.close[i] + derivadaMedia - df.close[i+1]) / df.close[i+1] * 100}")


4     49.28
5     48.90
6     48.76
7     48.39
8     48.45
9     48.36
10    48.65
11    48.26
12    48.34
Name: close, dtype: float64

'Calculando a derivada de 48.45 para 48.36'

'Derivada Centrada (passo 1): -0.015000000000000568; Previsto: 48.435; Erro: 0.1550868486352416'

'Derivada Centrada (passo 2): -0.027499999999999858; Previsto: 48.4225; Erro: 0.1292390405293631'

'Derivada Centrada de 4: -0.01083333333333473; Previsto: 48.439166666666665; Erro: 0.16370278467052465'

'Derivada Centrada de 4 (passo 2): 0.002500000000001279; Previsto: 48.4525; Erro: 0.19127377998345976'

'Derivada Centrada de 8): 0.02233928571428529; Previsto: 48.47233928571429; Erro: 0.23229794399150486'

'Derivada Média Geral: -0.005698809523809717; Previsto: 48.444301190476196; Erro: 0.1743200795620276'

In [10]:
std = 1.5

fig = go.Figure()
fig.update_layout(
    title="Teste de Runge Kuttas",
    xaxis_title="Erro em porcentagem",
    yaxis_title="Contagem",
    font_color="#cccccc", 
    plot_bgcolor='#1f1f1f', 
    paper_bgcolor='#181818',
    barmode='overlay'
)

for i in range(1, 4):
    rk_result, error = create_runge_kutta(df, rk_step=i*2, inplace=False, error=True)
    data = pd.Series([float(i)/0.38682969 for i in rk_result[[i for i in rk_result][0]].dropna(inplace=False)])

    fig.add_trace(
        go.Histogram(
            opacity=0.2, 
            name=f"RK Error (rk_step={i*2})", 
            x=pd.Series([float(i) for i in error[[i for i in error][0]].dropna(inplace=False)]), 
            xbins=dict(start=np.ceil(-(data.describe()["std"])*std), end=np.ceil((data.describe()["std"])*std) + 0.1, size=0.1)
        )
    )

fig.show()

NameError: name 'create_runge_kutta' is not defined

In [17]:
#create_runge_kutta(df, rk_step=i*2, derivation_step=j, inplace=True, error=True, direction=True)
df

time   open   high    low  close  tick_volume  spread  \
0     2022-04-11 10:00:00  48.00  48.11  47.90  48.06          285       1   
1     2022-04-11 10:15:00  48.08  48.16  47.87  47.99          399       1   
2     2022-04-11 10:30:00  47.99  49.01  47.85  49.01          623       1   
3     2022-04-11 10:45:00  49.00  49.00  48.54  48.74          130       1   
4     2022-04-11 11:00:00  48.68  49.51  48.68  49.28          168       1   
...                   ...    ...    ...    ...    ...          ...     ...   
20833 2025-02-13 12:45:00  64.27  64.57  64.16  64.20          162       0   
20834 2025-02-13 13:00:00  64.20  64.26  63.42  63.63          179       0   
20835 2025-02-13 13:15:00  63.65  63.81  63.40  63.52          160       0   
20836 2025-02-13 13:30:00  63.49  63.52  63.03  63.13          298       0   
20837 2025-02-13 13:45:00  63.18  63.41  63.18  63.38           46       0   

       real_volume     k1      k2      k3     k4 rk_close(2, 1)  \
0            70002   <NA>    <NA>    <NA>   <NA>           <NA>   
1            73269   <NA>    <NA>    <NA>   <NA>           <NA>   
2           173235  0.475  0.7825  0.2375  0.545          49.52   
3            67164  0.375 -0.4575  0.1875 -0.645         48.605   
4            48384  0.135  0.4725  0.0675  0.405          49.55   
...            ...    ...     ...     ...    ...            ...   
20833        36269   0.11  -0.105   0.055  -0.16         64.175   
20834        36980  -0.31  -0.415  -0.155  -0.26         63.345   
20835        33969  -0.34    0.06   -0.17   0.23         63.465   
20836        72617  -0.25  -0.265  -0.125  -0.14         62.935   
20837        10523  -0.07   0.285  -0.035   0.32         63.505   

      rk_error_close(2, 1)                    rk_direction_close(2, 1)  \
0                     <NA>                                        <NA>   
1                     <NA>                                        <NA>   
2                     0.78                                        <NA>   
3                   -0.675  0 - P:48.605000000000004; R:48.74; T:49.28   
4                     0.65   0 - P:49.550000000000004; R:49.28; T:48.9   
...                    ...                                         ...   
20833                0.545                                           1   
20834               -0.175                                           1   
20835                0.335                                           1   
20836               -0.445              0 - P:62.935; R:63.13; T:63.38   
20837                 <NA>                                        <NA>   

      rk_close(24166, 1) rk_error_close(24166, 1)  
0                   <NA>                     <NA>  
1                   <NA>                     <NA>  
2                  49.52                     0.78  
3                 48.605                   -0.675  
4                  49.55                     0.65  
...                  ...                      ...  
20833             64.175                    0.545  
20834             63.345                   -0.175  
20835             63.465                    0.335  
20836             62.935                   -0.445  
20837             63.505                     <NA>  

[20838 rows x 17 columns]

### Data Visualization

In [34]:
#df_plot
df[[i != 0 if type(i) != type(pd.NA) else False for i in df.strtgy_ma.values]].dropna().reset_index(drop=True)
df[[i > pd.Timestamp('2022-04-12') and i < pd.Timestamp('2022-04-13') if type(i) != type(pd.NA) else False for i in df.time.values]].dropna().reset_index(drop=True)
df.values[60]

AttributeError: 'DataFrame' object has no attribute 'strtgy_ma'

In [35]:
df_plot = df.dropna().reset_index(drop=True)

fig = go.Figure(go.Candlestick(
    x=df_plot.time,
    open=df_plot.open,
    high=df_plot.high,
    low=df_plot.low,
    close=df_plot.close,
    name='Candlesticks'
))

try:
    fig.add_traces(
        go.Line(
            x=df_plot.time,
            y=df_plot["moving_average_close(9)"],
            name='Moving Average (9)',
            line={'color':'#929292'}
        )
    )

    fig.add_traces(
        go.Line(
            x=df_plot.time,
            y=df_plot["moving_average_close(21)"],
            name='Moving Average (21)',
            line={'color':'#cccccc'}
        )
    )

    try:
        df_orders = df[[i != 0 if type(i) != type(pd.NA) else False for i in df.strtgy_ma.values]].dropna().reset_index(drop=True)
        display(df_orders.strtgy_ma[[False]+[df_orders.strtgy_ma[i] == df_orders.strtgy_ma[i-1] for i in range(1, len(df_orders.strtgy_ma))]])
        
        fig.add_traces(
            go.Scatter(
                x=df_orders[df_orders["strtgy_ma"] == 1].time,
                y=df_orders[df_orders["strtgy_ma"] == 1]["moving_average_close(9)"],
                name='Moving Average Strategy (Buy)',
                mode='markers',
                marker_color="green"
                #marker={"color": "green"}
            )
        )

        fig.add_traces(
            go.Scatter(
                x=df_orders[df_orders["strtgy_ma"] == -1].time,
                y=df_orders[df_orders["strtgy_ma"] == -1]["moving_average_close(9)"],
                name='Moving Average Strategy (Sell)',
                mode='markers',
                marker_color="red"
                #marker={"color": "red"}
            )
        )
    except:
        print("Sem Df_orders")
except:
    print("Sem Df_plot_Moving_Averages")

fig.update_layout(
    xaxis_rangeslider_visible=False, 
    height=700, 
    margin=dict(l=10,r=10,b=10,t=10), 
    font_color="#cccccc", 
    plot_bgcolor='#1f1f1f', 
    paper_bgcolor='#181818'
    )#, template='plotly_dark')

fig.update_xaxes(
    gridcolor ="#37373d",
    #fixedrange=False,
    rangeslider_visible=False,
    rangebreaks=[
        dict(bounds=["sat", "mon"]),               # Blacklist em finais de semana
        dict(bounds=[18.25, 10], pattern="hour"),  # Crop entre 10am e 6pm
        dict(values=[])                            # Blacklist para feriados "aaaa-mm-dd"
    ]
)

fig.update_yaxes(
    fixedrange=False, 
    gridcolor ="#37373d"
)

fig.show()

Sem Df_plot_Moving_Averages


In [31]:
df[df.close == 60.15]

time   open  high    low  close  tick_volume  spread  \
20777 2025-02-11 14:45:00  59.98  60.3  59.95  60.15          459       1   

       real_volume    k1    k2    k3    k4 rk_close(2, 1)  \
20777        42488 -0.08  0.21 -0.04  0.25         60.235   

      rk_error_close(2, 1)        rk_direction_close(2, 1) rk_close(24166, 1)  \
20777                0.585  0 - P:60.235; R:60.15; T:59.65             60.235   

      rk_error_close(24166, 1)  
20777                    0.585

In [28]:
# Dá crop nos dados pra não matar o vs code
df_plot = df[:][-130:].reset_index()

# Cria a base do gráfico de candle com os dados normais
fig = go.Figure(go.Candlestick(
    x=df_plot.time,
    open=df_plot.open,
    high=df_plot.high,
    low=df_plot.low,
    close=df_plot.close,
    name='Candlesticks'
))

#fig.add_traces(
#        go.Line(
#            x=df_plot.time,
#            y=df_plot.close,
#            name='Closes',
#            #mode='markers',
#            marker_color="brown"
#        )
#    )

try:
    # Separa os hammers
    hammer_df = df_plot[df_plot["is_hammer"] != 0]

    # Dá override nos candles martelo pintando eles de dourado
    fig.add_traces(
        go.Candlestick(
            x=hammer_df.time,
            open=hammer_df.open,
            high=hammer_df.high,
            low=hammer_df.low,
            close=hammer_df.close,
            name='Hammer Candlesticks',
            increasing ={'fillcolor':'gold', 'line':{'color':'gold'}},
            decreasing ={'fillcolor':'gold', 'line':{'color':'gold'}}
        )
    )
except:
    print("Sem Df_Hammer")

try:
    fig.add_traces(
        go.Line(
            x=df_plot.time,
            y=df_plot["moving_average_close(9)"],
            name='Moving Average (9)',
            line={'color':'#929292'}
        )
    )

    fig.add_traces(
        go.Line(
            x=df_plot.time,
            y=df_plot["moving_average_close(21)"],
            name='Moving Average (21)',
            line={'color':'#cccccc'}
        )
    )

    fig.add_traces(
        go.Scatter(
            x=df_plot[df_plot["strtgy_ma"] == 1].time,
            y=df_plot[df_plot["strtgy_ma"] == 1]["moving_average_close(9)"],
            name='Moving Average Strategy (Buy)',
            mode='markers',
            marker_color="green"
            #marker={"color": "green"}
        )
    )

    fig.add_traces(
        go.Scatter(
            x=df_plot[df_plot["strtgy_ma"] == -1].time,
            y=df_plot[df_plot["strtgy_ma"] == -1]["moving_average_close(9)"],
            name='Moving Average Strategy (Sell)',
            mode='markers',
            marker_color="red"
            #marker={"color": "red"}
        )
    )
except:
    print("Sem Df_Moving_Averages")

#try:
df_rk = pd.DataFrame({"time": [i for i in df_plot.time], 
                      "close": [i for i in df_plot.close], 
                      #"rk": [i[0] if type(i[0]) == float else 0 for i in df_plot["rk_close(2, 1)"]]})
                      "rk": [i for i in df_plot["rk_close(2, 1)"]]})

for i in range(len(df_rk) - 1):  # Exclude the last candle
    x_values = [df_rk['time'][i], df_rk['time'][i + 1]]  # Points for the line
    y_values = [df_rk['close'][i], df_rk['rk'][i] + np.random.uniform(-1, 1)]  # Add randomness to target
    fig.add_trace(go.Scatter(x=x_values, 
                            y=y_values, 
                            mode='lines', 
                            showlegend=False,
                            line=dict(color='gray', width=3)))  # Increase line width
    
if len(df) > 0:
    last_date = df_rk['time'].iloc[-1]

    x_values = [last_date, last_date + pd.tseries.offsets.Minute(15)]#pd.DateOffset(1)]
    y_values = [df_rk['close'].iloc[-1], df_rk['rk'].iloc[-1] + np.random.uniform(-1, 1)]
    fig.add_trace(go.Scatter(x=x_values, 
                            y=y_values, 
                            mode='lines', 
                            line=dict(color='gray', width=3)))
        
    #fig.add_traces(
    #    go.Line(
    #        x=df_rk.time,
    #        y=df_rk.rk,
    #        name='Runge Kutta Prediction',
    #        #mode='markers',
    #        marker_color="gold"
    #    )
    #)    

    #df_rk = pd.DataFrame({"time": [i for i in df_plot.time], "euler": [i[0] if type(i[0]) == float else 0 for i in create_runge_kutta(df_plot, rk_step=2, derivation_step=1, inplace=False)[1].values]})
    #fig.add_traces(
    #    go.Line(
    #        x=df_rk.time,
    #        y=df_rk.euler,
    #        name='Euler Prediction',
    #        #mode='markers',
    #        marker_color="gray"
    #    )
    #)
#except:
#    print("Sem Df_Runge_Kutta")


# Deixa o gráfico bonito parecido com o meu tema do vscode, se não não roda
fig.update_layout(
    xaxis_rangeslider_visible=False, 
    height=700, 
    margin=dict(l=10,r=10,b=10,t=10), 
    font_color="#cccccc", 
    plot_bgcolor='#1f1f1f', 
    paper_bgcolor='#181818'
    )#, template='plotly_dark')

fig.update_xaxes(
    gridcolor ="#37373d",
    #fixedrange=False,
    rangeslider_visible=False,
    rangebreaks=[
        dict(bounds=["sat", "mon"]),               # Blacklist em finais de semana
        dict(bounds=[18.25, 10], pattern="hour"),  # Crop entre 10am e 6pm
        dict(values=[])                            # Blacklist para feriados "aaaa-mm-dd"
    ]
)

fig.update_yaxes(
    fixedrange=False, 
    gridcolor ="#37373d"
)

fig.show()
display(df_plot[-15:])

Sem Df_Hammer
Sem Df_Moving_Averages


index                time   open   high    low  close  tick_volume  \
115  20823 2025-02-13 10:15:00  62.19  62.39  62.16  62.36          170   
116  20824 2025-02-13 10:30:00  62.38  62.88  61.78  62.79          562   
117  20825 2025-02-13 10:45:00  62.76  62.86  62.65  62.76          169   
118  20826 2025-02-13 11:00:00  62.75  62.90  62.66  62.73           96   
119  20827 2025-02-13 11:15:00  62.70  62.94  62.44  62.44          265   
120  20828 2025-02-13 11:30:00  62.49  63.15  62.07  63.15          839   
121  20829 2025-02-13 11:45:00  63.08  63.40  62.66  62.89          283   
122  20830 2025-02-13 12:00:00  62.92  63.72  62.89  63.71          395   
123  20831 2025-02-13 12:15:00  63.72  64.12  63.55  63.98          530   
124  20832 2025-02-13 12:30:00  63.92  64.51  63.92  64.25          253   
125  20833 2025-02-13 12:45:00  64.27  64.57  64.16  64.20          162   
126  20834 2025-02-13 13:00:00  64.20  64.26  63.42  63.63          179   
127  20835 2025-02-13 13:15:00  63.65  63.81  63.40  63.52          160   
128  20836 2025-02-13 13:30:00  63.49  63.52  63.03  63.13          298   
129  20837 2025-02-13 13:45:00  63.18  63.41  63.18  63.38           46   

     spread  real_volume     k1      k2      k3     k4 rk_close(2, 1)  \
115       0        45058   0.93  -0.295   0.465  -0.76         62.445   
116       0       116804    0.3    0.28    0.15   0.13         63.005   
117       0        29973    0.2   -0.13     0.1  -0.23         62.745   
118       0        30362  -0.03  -0.015  -0.015    0.0         62.715   
119       0        56848  -0.16   -0.21   -0.08  -0.13         62.295   
120       0       214796   0.21   0.605   0.105    0.5         63.505   
121       0        86587  0.225 -0.3725  0.1125 -0.485          62.76   
122       0        68643   0.28    0.68    0.14   0.54          64.12   
123       0        91213  0.545 -0.0025  0.2725 -0.275         64.115   
124       0        43969   0.27   0.135   0.135    0.0         64.385   
125       0        36269   0.11  -0.105   0.055  -0.16         64.175   
126       0        36980  -0.31  -0.415  -0.155  -0.26         63.345   
127       0        33969  -0.34    0.06   -0.17   0.23         63.465   
128       0        72617  -0.25  -0.265  -0.125  -0.14         62.935   
129       0        10523  -0.07   0.285  -0.035   0.32         63.505   

    rk_error_close(2, 1)                    rk_direction_close(2, 1)  \
115               -0.345                                           1   
116                0.245              0 - P:63.005; R:62.79; T:62.76   
117                0.015                                           1   
118                0.275                                           1   
119               -0.855              0 - P:62.295; R:62.44; T:63.15   
120                0.615  0 - P:63.504999999999995; R:63.15; T:62.89   
121                -0.95  0 - P:62.760000000000005; R:62.89; T:63.71   
122                 0.14                                           1   
123               -0.135                                           1   
124                0.185               0 - P:64.385; R:64.25; T:64.2   
125                0.545                                           1   
126               -0.175                                           1   
127                0.335                                           1   
128               -0.445              0 - P:62.935; R:63.13; T:63.38   
129                 <NA>                                        <NA>   

    rk_close(24166, 1) rk_error_close(24166, 1)  
115             62.445                   -0.345  
116             63.005                    0.245  
117             62.745                    0.015  
118             62.715                    0.275  
119             62.295                   -0.855  
120             63.505                    0.615  
121              62.76                    -0.95  
122              64.12                     0.14  
123             64.115          

In [ ]:
import plotly.graph_objects as go
import pandas as pd
import numpy as np

# Sample data (replace with your actual data)
data = {'Date': pd.date_range('2023-01-01', periods=10),
        'Open': [100, 102, 98, 101, 99, 105, 103, 107, 104, 106],
        'High': [103, 105, 100, 103, 101, 107, 105, 109, 106, 108],
        'Low': [98, 100, 96, 99, 97, 103, 101, 105, 102, 104],
        'Close': [101, 103, 99, 102, 100, 106, 104, 108, 105, 107],
        'Target': [105, 107, 102, 106, 104, 110, 108, 112, 109, 111]}

df = pd.DataFrame(data)

# Create the candlestick chart
fig = go.Figure(data=[go.Candlestick(x=df['Date'],
                                    open=df['Open'],
                                    high=df['High'],
                                    low=df['Low'],
                                    close=df['Close'])])

# Add bolder lines from close to target points with some randomness
for i in range(len(df) - 1):  # Exclude the last candle
    x_values = [df['Date'][i], df['Date'][i + 1]]  # Points for the line
    y_values = [df['Close'][i], df['Target'][i] + np.random.uniform(-1, 1)]  # Add randomness to target
    fig.add_trace(go.Scatter(x=x_values, 
                            y=y_values, 
                            mode='lines', 
                            line=dict(color='red', width=3)))  # Increase line width

# Add a line for the last candle (if it exists)
if len(df) > 0:
    last_date = df['Date'].iloc[-1]
    next_date = last_date + pd.DateOffset(1)  # Calculate the next date

    x_values = [last_date, next_date]
    y_values = [df['Close'].iloc[-1], df['Target'].iloc[-1] + np.random.uniform(-1, 1)]
    fig.add_trace(go.Scatter(x=x_values, 
                            y=y_values, 
                            mode='lines', 
                            line=dict(color='red', width=3)))

# Customize the layout (optional)
fig.update_layout(
    title='Candlestick Chart with Bolder Target Lines',
    xaxis_title='Date',
    yaxis_title='Price'
)

# Show the plot
fig.show()

In [16]:
df[[i != 0 if type(i) != type(pd.NA) else False for i in df["rk_close(2, 1)"].values]].dropna().reset_index(drop=True)
df[[i > pd.Timestamp('2022-03-27') and i < pd.Timestamp('2022-03-28') if type(i) != type(pd.NA) else False for i in df.time.values]].dropna().reset_index(drop=True)
[i for i in df["rk_direction_close(2, 1)"].values]

KeyError: 'rk_close(2, 1)'

## Testes 
https://hub.asimov.academy/blog/como-enviar-ordens-no-metatrader5/ 

In [23]:
def error_quit(message):
    print(message)
    mt5.shutdown(); quit()

def check_volume(vol, symbol):
    maxvol = mt5.symbol_info(symbol).volumehigh
    minvol = mt5.symbol_info(symbol).volumelow
    if vol < minvol or vol > maxvol:
        error_quit(f'Volume Selecionado: {vol}\nVolume Mínimo: {minvol}\nVolume Máximo: {maxvol}')

def order_result_log(result_object):
    # solicitamos o resultado na forma de dicionário e exibimos elemento por elemento
    result_dict = result_object._asdict()
    for field in result_dict.keys():
        print(f"   {field}={result_dict[field]}")
        #se esta for uma estrutura de uma solicitação de negociação, também a exibiremos elemento a elemento
        if field == "request":
            traderequest_dict = result_dict[field]._asdict()
            for tradereq_filed in traderequest_dict:
                print(f"\ttraderequest: {tradereq_filed}={traderequest_dict[tradereq_filed]}")

In [ ]:
# preparamos o ativo
symbol="ITUB4"
symbol_info = mt5.symbol_info(symbol)
if symbol_info is None:
    error_quit(f"{symbol} não foi encontrado, não é possível chamar order_check()")
   
 
# se o símbolo não estiver disponível no MarketWatch, adicionamos
if not symbol_info.visible:
    print(symbol, "não está visível, tentando conectar...")
    if not mt5.symbol_select(symbol,True):
        error_quit(f"symbol_select({symbol}) falhou, exiting...")

point = mt5.symbol_info(symbol).point
ask = mt5.symbol_info_tick(symbol).ask

# estabelecer o volume aqui para mitigar erros
volume = 100.0
check_volume(volume, symbol)

request = {
    "action": mt5.TRADE_ACTION_DEAL,            # TRADE_ACTION_DEAL -> Ordem imediata
    "symbol": symbol,
    "volume": volume,                          
    "type": mt5.ORDER_TYPE_BUY,                 # ORDER_TYPE_BUY -> Ordem para compra
    "price": ask,                               # preço ask
    "sl": ask-100*point,
    "tp": ask+100*point,
    "deviation": 10,
    "magic": 234000,
    "comment": "asimov python script",
    "type_time": mt5.ORDER_TIME_GTC,            # ORDER_TIME_GTC -> A ordem permanecerá na fila até ser tirada
    "type_filling": mt5.ORDER_FILLING_RETURN,   # ORDER_FILLING RETURN -> No caso de uma execução parcial, a ordem de mercado ou limit com um volume residual não é retirada e continua
}

result = mt5.order_check(request)
result = mt5.order_send(request)

if result.retcode != mt5.TRADE_RETCODE_DONE:
    order_result_log(result); error_quit()

### Redes neurais

In [ ]:
#from lazypredict.Supervised import LazyRegressor#, LazyClassifier
from sklearn.model_selection import train_test_split
#from sklearn.preprocessing import StandardScaler
#from sklearn.pipeline import make_pipeline
from sklearn.linear_model  import LinearRegression

In [ ]:
df['next_close'] = df['close'].shift(-1)
df.dropna(inplace=True)

X = df[['close']]
y = df['next_close']

# Split data into training and testing sets
train_size = int(len(df) * 0.7)
train_data, test_data = df[0:train_size], df[train_size:]

# Train the Linear Regression model
model = LinearRegression()
model.fit(train_data[['close']], train_data['next_close'])

# Make predictions on the test data
test_data['Predictions'] = model.predict(test_data[['close']])

# Create a Plotly figure
fig = go.Figure()

# Add actual closing prices
fig.add_trace(go.Scatter(x=test_data.index, y=test_data['close'], name='Actual'))

# Add predicted closing prices
fig.add_trace(go.Scatter(x=test_data.index, y=test_data['Predictions'], name='Predicted'))

# Customize the plot
fig.update_layout(
    title='Stock Price Prediction',
    xaxis_title='Date',
    yaxis_title='Closing Price',
    legend=dict(
        x=0,
        y=1.0,
        bgcolor='rgba(255, 255, 255, 0)',
        bordercolor='rgba(255, 255, 255, 0)'
    )
)

# Show the plot
fig.show()

In [ ]:
x = df.drop("close", axis=1)
y = df["close"]

X_train, X_test, y_train, y_test = train_test_split(x, y, test_size=0.3, random_state=42)

reg = LazyRegressor(verbose=0, ignore_warnings=True, custom_metric=None)
models, predictions = reg.fit(X_train, X_test, y_train, y_test)

models

In [ ]:
a = model.predict([[74.98]])#, 75.24, 74.98, 74.94, 74.77, 75.37, 76.30]])
a